# Kenya Real Estate Prices Prediction

There are many factors that can influence the real estate of any country. In this lab, we are going to analyse the physical locations of these properties in order to find geographical patterns.

## Objectives


This lab contains the following tasks:

*   **TASK 1:** Mark all the Kenyan counties on a map
*   **TASK 2:** Mark the property types for all the counties on the map



Import useful libraries:

In [1]:
import folium
import pandas as pd
import numpy as np

In [2]:
# Import folium MarkerCluster plugin
from folium.plugins import MarkerCluster
# Import folium MousePosition plugin
from folium.plugins import MousePosition
# Import folium DivIcon plugin
from folium.features import DivIcon

Import the Real Estate Dataset

In [3]:
real_estate = pd.read_csv('Real_Estate_Data.csv')
real_estate.head(5)

Title  \
0      5 Bedroom House For Sale In Parklands   
1                    Land For Sale In Kilifi   
2             0.5 Ac Land For Sale In Tigoni   
3  3 Bedroom Apartment For Sale In Thindigua   
4   2 Bedroom Apartment For Sale In Kilimani   

                                                 URL  Bedrooms  Bathrooms  \
0  https://www.buyrentkenya.com/listings/5-bedroo...       5.0        3.0   
1  https://www.buyrentkenya.com/listings/land-for...       NaN        NaN   
2  https://www.buyrentkenya.com/listings/05-ac-la...       NaN        NaN   
3  https://www.buyrentkenya.com/listings/3-bedroo...       3.0        NaN   
4  https://www.buyrentkenya.com/listings/2-bedroo...       2.0        2.0   

                                  Location Property Type  Price ($)  \
0  Off 2nd Parklands, Parklands, Westlands         House  362850.97   
1                     Kilifi, Kilifi North          Land  302375.81   
2                   Tigoni, Tigoni, Limuru          Land   86393.09   
3                     Thindigua, Thindigua     Apartment  112311.02   
4                Kilimani, Dagoretti North     Apartment   99352.05   

   Size (m²)    County  
0        NaN  Nairobi   
1        NaN   Kilifi   
2        NaN   Kiambu   
3        NaN       NaN  
4      125.0  Nairobi

In [4]:
# Remove unnecessary whitespace after county name
real_estate['County'] = real_estate['County'].str.rstrip()

Import dataset with latitude and longitude coordinates of different counties:

In [5]:
geo = pd.read_excel('county_locations.xlsx')
geo.head(5)

County Lattitude Longitude
0       Kiambu  -1.16667  36.83333
1     Murang'a  -0.71667     37.15
2      Kajiado  -1.85238  36.77683
3  Uasin Gishu    0.5000   35.3167
4       Kilifi  -3.63045  39.84992

### Construction of Map:

We first need to create a folium Map object, with an initial center location to be Kenya's capital city, Nairobi.

In [6]:
# Start location is Nairobi, Kenya
nairobi_coordinate = [-1.386389, 36.817223]
site_map = folium.Map(location=nairobi_coordinate, zoom_start=5.5)

In [7]:
site_map

## Task 1: Mark all the Kenyan counties on the map

Now, let's add a circle for each County with properties for sale:

In [8]:
col = geo.columns

# save coordinates in lists
counties = [v for k,v in geo[col[0]].items()]
lat = [v for k,v in geo[col[1]].items()]
long = [v for k,v in geo[col[2]].items()]
circles = []

for i in range(len(counties)):
    coordinate = [lat[i], long[i]]
    # circle objects
    circle = folium.Circle(coordinate, radius=100, color='#000000', fill=True).add_child(folium.Popup(f'{counties[i]}'))
    
    # marker objects
    marker = folium.map.Marker(coordinate, icon=DivIcon(icon_size=(40,40),icon_anchor=(0,0), 
                                               html='<div style="font-size: 12; color:#d35400;"><b>%s</b></div>' % f'{counties[i]}', ))
    site_map.add_child(circle)
    site_map.add_child(marker)
    
site_map

**Observation:** 
* We can see that most counties with properties for sale are located towards the south of Kenya. 
* No one posted properties for sale in Northern Kenya.

##   **TASK 2:** Mark the property types for all the counties on the map


First create a MarkerCluster object

In [9]:
marker_cluster = MarkerCluster()

 Create a new column in the dataframe called `marker_color` to store the marker colors based on the `Property Type`.

In [10]:
# Function to assign color to launch outcome
def assign_marker_color(property_type):
    if property_type == 'House':
        return 'green'
    elif property_type == 'Apartment':
        return 'blue'
    elif property_type == 'Land':
        return 'red'
    
real_estate['marker_color'] = real_estate['Property Type'].apply(assign_marker_color)
real_estate.tail(4)

Title  \
6940  500 M² Residential Land For Sale In Ongata Rongai   
6941         1 Bedroom Apartment For Sale In Kileleshwa   
6942              5 Bedroom Villa For Sale In Lavington   
6943         12.5 Ac Commercial Land For Sale In Tigoni   

                                                    URL  Bedrooms  Bathrooms  \
6940  https://www.buyrentkenya.com/listings/500-m2-r...       NaN        NaN   
6941  https://www.buyrentkenya.com/listings/1-bedroo...       1.0        1.0   
6942  https://www.buyrentkenya.com/listings/5-bedroo...       5.0        5.0   
6943  https://www.buyrentkenya.com/listings/125-ac-c...       NaN        NaN   

                                     Location Property Type   Price ($)  \
6940             Ongata Rongai, Kajiado North          Land    30237.58   
6941  Kileleshwa, Kileleshwa, Dagoretti North     Apartment    56155.51   
6942               Lavington, Dagoretti North         House   734341.25   
6943              Riara Ridge, Tigoni, Limuru          Land  1727861.77   

      Size (m²)   County marker_color  
6940      500.0   Nakuru          red  
6941       66.0  Nairobi         blue  
6942        NaN  Nairobi        green  
6943    48564.0   Kiambu          red

Create a function to access the `Latitude` and `Longitude` of any county.

In [11]:
def get_coordinate(county_name):
    
    if county_name == 'Tharaka Nithi':   # Name on real_estate dataset doesn't match name on geo coordinates dataset
        mask = geo['County'] == 'Tharaka-Nithi'
        latitude = geo[mask].iloc[0]['Lattitude']
        longitude = geo[mask].iloc[0]['Longitude']
        
    elif county_name == 'Murang’a':    # Name on real_estate dataset doesn't match name on geo coordinates dataset
        mask = geo['County'] == "Murang'a"
        latitude = geo[mask].iloc[0]['Lattitude']
        longitude = geo[mask].iloc[0]['Longitude']
        
    else :
        mask = geo['County'] == county_name
        latitude = geo[mask].iloc[0]['Lattitude']
        longitude = geo[mask].iloc[0]['Longitude']
    
    return latitude, longitude

For each property type in `real_estate` data frame, add a `folium.Marker` to `marker_cluster`

In [12]:
# Add marker_cluster to current site_map
site_map.add_child(marker_cluster)

# for each row in real_estate data frame
# create a Marker object with its coordinate
# and customize the Marker's icon property to indicate if this property is a house, apartment or land, 
# e.g., icon=folium.Icon(color='white', icon_color=row['marker_color']
for index, record in real_estate.dropna(subset=['County']).iterrows():
    
    label = record[8]
    property_type = record[5]
    lat, long = get_coordinate(label)
    row_color = record[9]
    
    # TODO: Create and add a Marker cluster to the site map
    marker = folium.Marker(
        location = [lat, long],
        popup = property_type,
        icon=folium.Icon(color='white', icon_color=row_color)
    )
    marker_cluster.add_child(marker)

Add a map feature that lets the user calculate latitude and longitude by hovering a mouse over the map.

In [13]:
# Add Mouse Position to get the coordinate (Lat, Long) for a mouse over on the map
formatter = "function(num) {return L.Util.formatNum(num, 5);};"
mouse_position = MousePosition(
    position='topright',
    separator=' Long: ',
    empty_string='NaN',
    lng_first=False,
    num_digits=20,
    prefix='Lat:',
    lat_formatter=formatter,
    lng_formatter=formatter,
)

site_map.add_child(mouse_position)
site_map.fit_bounds([[0.53283, 34.88708], [-2.08145, 38.12256]])
site_map

|  Map Object | Colour |
  | ----------------- | ------- |
 | House      | **<span style="color:#2E8B57">Green</span>**     |
  | Land       | **<span style="color:#DC143C"> Red </span>**     | 
  | Apartment        | **<span style="color:#000080">Dark Blue</span>**     | 


**Observation:** It appears that the new additions on the map support our earlier hypothesis that real estate owners are selling property closer to the south of Kenya. We can see that the highest number of properties for sale are in **Kajiado** and **Nairobi** which are closer to the south.

## Authors

<a href="https://www.linkedin.com/in/molomunyansanga/">Molo Munyansanga</a> is a Data Science enthusiast with certificates in Statistics, Data Science and Machine Learning. He has also completed the Deep Learning Specialization by DeepLearning.AI

## Change Log

| Date (YYYY-MM-DD) | Version | Changed By    | Change Description      |
| ----------------- | ------- | ------------- | ----------------------- |
| 2022-10-08        | 1     | Molo. M       | Created Notebook and Completed Tasks         |